MBS Example queries
==========================

Load iris
----------

In [1]:
load_ext iris

Import libraries
------------------

In [3]:
import py1010
import tenFrame as tf
import pandas as pd
import numpy as np
session = py1010.Session("1010data URL", "USERNAME", "PASSWORD", py1010.POSSESS)

MBS query examples
--------------------------
[Example 1: Agency pools](#Example-1:-Agency-pools)

[Example 2: Historical cohort](#Example-2:-Historical-cohort)

[Example 3: Cohort and S curve](#Example-3:-Cohort-and-S-curve)

[Example 4: CPR by occupancy type](#Example-4:-CPR-by-occupancy-type)

[Example 5: GNMA prepayment and buyout CPR](#Example-5:-GNMA-prepayment-and-buyout-CPR)

[Example 6: Loan level FHLMC CPR](#Example-6:-Loan-level-FHLMC-CPR)


Example 1: Agency pools
-----------------------------

This example computes the number of Agency Pools for each agency/gse (FNMA/FHLMC/GNMA) that have loans in each state for each month. The results show the outstanding balance of those loans and the number of loans. For instance, in Sept of 2022, there were 106,117 Freddie Mac Pools that had at least one active loan in CA, there was an approximately $510 billion balance and 1.578 million loans.

In [4]:
geo = tf.TenFrame(session, "pub.fin.embs.combined.stnd_pool.geo")
geo = geo[(geo.rectype == "G") & (geo.value != "ZZ")]
geo = geo.merge("pub.fin.embs.combined.stnd_pool.sec", on="issueid")
geo = geo[geo.colltype == "LOAN"]
geo = geo.groupby(["value", "agency", "effdt"]).agg({"value": "cnt", "rpb": "sum", "loans": "sum"})
geo2 = geo[geo.rpb_sum == geo.groupby(["value", "agency"]).rpb_sum.max(adjoin=True)['rpb_sum_max']]
# Hide that last column.
rv = geo2 = geo2[["value", "agency", "effdt", "value_cnt", "rpb_sum", "loans_sum"]]
geo2 = geo2.sort_values(by=["agency", "value", "effdt"], ascending=True)
geo2

TentenException: ('function run failed, returned 1 (Table is no longer accessible: pub.fin.embs.combined.stnd_pool.sec)', 1)

Example 2: Historical cohort
----------------------------------
This example shows the historical cohort (product, origination year, coupon) prepayment speeds (CPR) for the largest 10 cohorts (determined by the largest monthly outstanding balance for each cohort).

**_Note:_** g_tshift() is a 1010data function that returns the value of the first row that is a specified time period before (or after) the current row within a given group.

In [6]:
fh = tf.TenFrame(session, "pub.fin.embs.combined.stnd_pool.fh")
fh = fh.merge("pub.fin.embs.combined.stnd_pool.sec", on="issueid")
fh = fh[fh.colltype == 'LOAN']
fh = fh.merge("pub.fin.embs.combined.stnd_pool.sc", on="secid")
fh = fh[fh["coupontype"] == 'FIX']
fh["balance"] = fh.issamt * fh.fctr
fh["wam2"] = tf.select([fh.product.str.endswith('BALL')],
                    [fh.wam + (fh.waolterm - fh.origwam)], fh.wam)
fh["n_schedbal"] = fh.balance * fh.wac.amort(fh.wam2, 1)
# Adding aggregated columns needs to be done via "adjoin"
fh = fh.groupby("issueid").effdt.tshift("M", fh.n_schedbal, -1, name="schedbal", adjoin=True)
fh = fh[fh.schedbal.notnull()]
fh = fh[fh.coupon - tf.func.int(fh.coupon) == 0.5]
#Note the use of columnparams below, in order to supply the "weight"
# parameter to the wavg (weighted average) function.  When there are
# columnparams, any columns which don't have columnparams applied to them
# are moved to the end, so we have to add extra entries to columnparams for
# the first two columns to keep them in place.
fh2 = fh.groupby(["effdt", "coupon", "product", "productionyear"]).agg(
                 {"balance": "sum",
                  "schedbal": "sum",
                  "wac": "wavg",
                  "issueid": "cnt"},
                 columnparams=[
                     {"source":"balance", "fun":"sum"},
                     {"source":"schedbal", "fun":"sum"},
                     {"source":"wac", "fun":"wavg", "weight":"balance"}])
fh2["smm"] = 1 - fh2.balance_sum / fh2.schedbal_sum
fh2["cpr"] = tf.func.smm2cpr(100 * fh.smm)
fh2 = fh2.groupby(["coupon", "product", "productionyear"]).balance_sum.max(name="hibal", adjoin=True)
fh2 = fh2.hibal.rankuniq(name="rank", adjoin=True)
fh2 = fh2[fh2.rank < 10]
fh3 = fh2.groupby("effdt").agg({"cpr":"first", "balance_sum":"first"},
   cbreaks=["coupon", "product", "productionyear"])
fh3 = fh3.sort_values("effdt", ascending=False)
fh3

effdt  cpr_first  balance_sum_first       m0_0          m1_0  \
0  2023-05-01   7.551422       6.155347e+09   7.551422  6.155347e+09   
1  2023-04-01  10.176298       6.219424e+09  10.176298  6.219424e+09   
2  2023-03-01   6.923035       6.299078e+09   6.923035  6.299078e+09   
3  2023-02-01   6.638849       6.360679e+09   6.638849  6.360679e+09   
4  2023-01-01   8.560410       6.421076e+09   8.560410  6.421076e+09   
5  2022-12-01   7.965184       6.493097e+09   7.965184  6.493097e+09   
6  2022-11-01   9.171749       6.562180e+09   9.171749  6.562180e+09   
7  2022-10-01   9.331575       6.639110e+09   9.331575  6.639110e+09   
8  2022-09-01  12.208626       6.717747e+09  12.208626  6.717747e+09   
9  2022-08-01  11.193285       6.815417e+09  11.193285  6.815417e+09   

        m0_1          m1_1       m0_2          m1_2      m0_3  ...      m0_4  \
0   8.364425  3.414427e+09   7.940901  8.710077e+09  5.034537  ...  4.447350   
1  10.253989  3.463122e+09   8.862895  8.803715e+09  5.577155  ...  4.767520   
2   8.491458  3.518356e+09   7.014888  8.905567e+09  4.086964  ...  3.354534   
3   8.200441  3.568420e+09   6.443514  8.993283e+09  3.633648  ...  2.899536   
4   9.337242  3.617976e+09   7.983298  9.076968e+09  4.722760  ...  3.664120   
5   8.737023  3.671774e+09   7.984983  9.173842e+09  5.044684  ...  3.839919   
6   9.725223  3.724057e+09   8.897952  9.271504e+09  6.165357  ...  4.577213   
7  10.927611  3.780252e+09   9.891982  9.377727e+09  7.503026  ...  5.663559   
8  12.224130  3.841322e+09  11.732214  9.493578e+09  8.752840  ...  6.267672   
9  11.680567  3.907882e+09  10.771443  9.627134e+09  8.938142  ...  6.026088   

           m1_4       m0_5          m1_5      m0_6          m1_6      m0_7  \
0  2.773405e+11   7.458452  1.264448e+11  6.528973  2.097927e+11  5.196293   
1  2.789069e+11   8.036866  1.275271e+11  6.883293  2.112335e+11  5.428822   
2  2.805580e+11   6.112413  1.286847e+11  4.940399  2.126703e+11  4.079877   
3  2.818702e+11   5.245387  1.296276e+11  4.286861  2.136593e+11  3.534672   
4  2.830753e+11   6.563089  1.304762e+11  5.135386  2.148522e+11  4.658123   
5  2.844705e+11   6.989057  1.314822e+11  5.459254  2.162104e+11  4.988750   
6  2.859134e+11   9.110708  1.325453e+11  7.127829  2.176375e+11  6.060476   
7  2.875456e+11  11.114502  1.338729e+11  9.000910  2.193973e+11  7.427075   
8  2.894606e+11  13.363483  1.354641e+11  9.724405  2.215454e+11  8.870006   
9  2.915363e+11  13.370939  1.373659e+11  9.287666  2.238616e+11  8.883702   

           m1_7      m0_8          m1_8  
0  2.219410e+11  4.481145  3.205426e+11  
1  2.233633e+11  4.741509  3.223613e+11  
2  2.248382e+11  3.356946  3.242612e+11  
3  2.260537e+11  2.847907  3.257775e+11  
4  2.271662e+11  3.613349  3.271547e+11  
5  2.285050e+11  3.854936  3.287515e+11  
6  2.299160e+11  4.693048  3.304224e+11  
7  2.315523e+11  5.672905  3.323160e+11  
8  2.334830e+11  6.510854  3.345310e+11  
9  2.357358e+11  6.207307  3.370083e+11  

[10 rows x 21 columns]

Example 3: Cohort and S curve
-------------------------------------
This example shows cohort (product, origination year, and coupon) and S curve (CPR by rate incentive) with 50 basis point incentive buckets.

In [7]:
fh = tf.TenFrame(session, "pub.fin.embs.combined.stnd_pool.fh")
fh = fh.merge("pub.fin.embs.combined.stnd_pool.sec", on="secid")
fh = fh.merge("pub.fin.embs.combined.stnd_pool.sc", on="secid")
fh['linkmonth'] = fh.effdt.shiftmonths(-1,0).yrmo()
fh = fh.merge("pub.fin.econ.rates.pmms.nm", on="linkmonth", right_on="month")
fh['origterm'] = fh.origwam + fh.origwala
fh['benchmark_rate'] = tf.select([fh.coupontype == 'ARM', fh.origterm <= 180],
                               [fh.r51, fh.r15], fh.r30)
fh["incentive"] = fh["wac"] - fh["benchmark_rate"]
roundto = 0.5

# 1010data .round() is not exactly the same as pandas .round().
# it appears that pandas col.round(x) is equivalent to tenFrame
# col.round(10**-x)

fh["rincentive"] = fh.incentive.round(0.5)
fh["origmonth"] = fh.effdt.shiftmonths(-fh.wala, 0)
fh['origmonth'].setasdate()  # mark this column as a date.
fh["vintage"] = fh.origmonth.year()
fh["curbal"] =  fh.issamt * fh.fctr
fh["amortfctr"] = fh.wac.amort(fh.wam, 1)
fh["schedbal"] = fh.curbal * fh.amortfctr
fh["smmdec"] =  fh.cprm / 100
fh2 = fh[fh.colltype == 'LOAN']
fh3 = fh2.groupby(["product","coupon","productionyear","rincentive"]).agg(
 {"smmdec" : "wavg", "curbal": "sum"},
 breakelts={"col":"rincentive", "sort":"up"},
 columnparams=[{"source":"smmdec", "fun":"wavg", "weight": "schedbal", "name": "smm"}])
fh3['cpr'] = 100 * (1 - (1 - fh3.smm)**12)
fh3 = fh3[fh3.cpr.notnull()]
limit = 500000000
fh3 = fh3[fh3.curbal_sum >= limit]
fh3 = fh3[["product", "coupon", "productionyear", "rincentive", "cpr"]]
fh3.sort_values("rincentive", inplace=True)
rv = fh3[fh3.rincentive.notnull()]
rv

product  coupon  productionyear  rincentive       cpr
0  GNMII30M     1.5            2021        -5.0  3.455016
1    FHLN30     1.5            2020        -4.5  3.149840
2    FHLN20     1.5            2020        -4.5  2.234404
3  FHLR30JM     1.5            2020        -4.5  1.261580
4    FHLN30     1.5            2021        -4.5  2.487726
5    FHLN20     1.5            2021        -4.5  2.401478
6  FHLR30JM     1.5            2021        -4.5  1.186256
7    FHLN30     2.0            2021        -4.5  2.844877
8    FHLN15     1.0            2021        -4.5  2.409650
9  GNMII30M     2.0            2020        -4.5  5.666838

Example 4: CPR by occupancy type
------------------------------------------
This example shows prepayments (CPR) by occupancy type (owner/investor/second home) for FHLMC GOLD 30 Year 2012 Production 4% pools.

In [8]:
ldst = tf.TenFrame(session, "pub.fin.embs.combined.stnd_pool.ldst_orig")
ldst = ldst[ldst.rectype == 'O']
ldst = ldst[ldst.rpb > 0]
ldst = ldst.merge("pub.fin.embs.combined.stnd_pool.fh", on=["issueid", "effdt"])
ldst = tf.merge(ldst, "pub.fin.embs.combined.stnd_pool.sec", on="issueid")
ldst = ldst[(ldst.colltype == 'LOAN') & (ldst.product == 'FHLG30')]
ldst = ldst.merge("pub.fin.embs.combined.stnd_pool.sc", on="secid")
ldst = ldst[(ldst.coupon == 4) & (ldst.productionyear == 2012)]
ldst["nschedbal"] = ldst.rpb * ldst.wac.amort(ldst.wam, 1)
ldst = ldst.groupby(["issueid", "value1"]).effdt.tshift('M', ldst.nschedbal, -1, adjoin=True, name="schedbal")
ldst["prepaybal"] = ldst.schedbal.notnull() * ldst.rpb
ldst2 = ldst.groupby(["value1", "effdt"]).agg({"value1":"cnt", "schedbal":"sum", "prepaybal":"sum"})
ldst2["smm"] = 1 - ldst2.prepaybal_sum / ldst2.schedbal_sum
ldst2["cpr"] = tf.func.smm2cpr(100 * ldst2.smm)
rv = ldst3 = ldst2.groupby("effdt").agg({"cpr":"first"}, cbreaks="value1")
ldst3

effdt  cpr_first        m0        m1        m2
0  2012-01-01        NaN       NaN       NaN       NaN
1  2012-02-01   0.138066  0.138066  0.631807 -0.149019
2  2012-03-01   0.100135  0.100135  1.499251  1.216603
3  2012-04-01   2.052755  2.052755  1.611028  1.795059
4  2012-05-01   5.815703  5.815703  2.887672  1.819906
5  2012-06-01   6.227530  6.227530  4.307487  2.624381
6  2012-07-01   3.951870  3.951870  5.707675  5.448023
7  2012-08-01   7.165242  7.165242  8.160101  7.995545
8  2012-09-01   6.397460  6.397460  9.898887  8.490837
9  2012-10-01   8.277151  8.277151  9.053104  9.126371

Example 5: GNMA prepayment and buyout CPR
--------------------------------------------------------
This example shows loan level GNMA prepayment and buyout CPR and outstanding principal balance for GNMA 30 Year 4% coupon 2014 production year.

In [9]:
gll = tf.TenFrame(session, "pub.fin.embs.combined.loan.gll")
gll = gll[gll.updsrc == "GLLM"]
# The original was a little more complicated; easier this way around.
gll['rpb'] = tf.select([(gll.currmonliquidationflag == 'Y'), gll.currrpb.notnull(), gll.currrpb.isnull()],
                    [0, gll.currrpb, gll.origloanamt * gll.noterate.amort(gll.origterm, gll.loanage)])
gll = gll.merge("pub.fin.embs.combined.stnd_pool.sec", on="secmnem")
gll = gll.merge("pub.fin.embs.combined.stnd_pool.sc", on="secmnem")
gll = gll[(gll.product == "GNM30") & (gll.coupon == 4) & (gll.productionyear == 2014)]
gll['sbal'] = gll.rpb * gll.noterate.amort(gll.remterm, 1)
gll = gll.groupby(["secmnem", "loanseqnum"]).fctrdt.tshift("M", gll.sbal, -1, adjoin=True, name="schedbal")
gll = gll.groupby(["secmnem", "loanseqnum"]).fctrdt.tshift("M", gll.rpb, -1, adjoin=True, name="prev_rpb")
gll = gll.resetbreaks() # ?? needed??
# For the following, could I just do (gll.currmonliquidationflag == "Y") * gll.prev_rpb?
gll['prepays'] = tf.select([gll.currmonliquidationflag == "Y"], [gll.prev_rpb])
# I'll even do it that way here:
gll['buyouts'] = (gll.removalreasoncode == 2) * gll.currrpb
gll2 = gll.groupby("fctrdt").agg({"rpb":"sum", "schedbal":"sum", "prepays":"sum", "buyouts":"sum"},
                             breakelts={"col":"fctrdt", "sort":"up"})
gll2['smm'] = gll2.prepays_sum / gll2.schedbal_sum
gll2['cpr'] = 100 * (1 - (1 - gll2.smm)**12)
gll2['smm_buyout'] = gll2.buyouts_sum / gll2.schedbal_sum
gll2['cpr_buyout'] = 100 * (1 - (1 - gll2.smm_buyout)**12)
rv = gll2[['fctrdt', 'rpb_sum', 'cpr', 'cpr_buyout']]
rv

fctrdt       rpb_sum       cpr  cpr_buyout
0  2014-02-01  5.116197e+07       NaN         NaN
1  2014-03-01  3.578247e+08  0.000000    0.000000
2  2014-04-01  8.940600e+08  1.447868    0.000000
3  2014-05-01  1.155273e+09  1.610689    0.000000
4  2014-06-01  1.486189e+09  2.449771    0.000000
5  2014-07-01  1.613737e+09  2.665512    0.000000
6  2014-08-01  1.777851e+09  3.843906    0.000000
7  2014-09-01  2.186035e+09  6.041507    0.352740
8  2014-10-01  2.632772e+09  7.235836    0.901366
9  2014-11-01  2.788967e+09  7.805672    1.361744

Example 6: Loan level FHLMC CPR
------------------------------------------
This example displays loan level CPR. There is no 0 balance record supplied, so CPR is computed using a forward scheduled balance calculation compared with next months balance. If there is no record then a payoff has occured. The maximum factor date for the table is computed as to not consider empty records as a prepay.

In [10]:
ll = tf.TenFrame(session, "pub.fin.embs.combined.loan.ll")
ll = ll[ll.updsrc == 'FHML']
ll_2 = ll.agg({"fctrdt": ["cnt", "max"]})
# merge with on=1 ??  That's what the XML needs, but I doubt it makes sense in pandas!
ll = ll.merge(ll_2, on=1)
ll['schedbal'] = ll.currrpb * ll.orignoterate.amort(ll.remterm, 1)
ll = ll.groupby(["secmnem", "loanseqnum"]).fctrdt.tshift("M", ll.currrpb, 1, adjoin=True, name="nextbal_raw")
# This just trims off a single row...
ll = ll[ll.fctrdt < ll.fctrdt_max]
# I guess I can't really use ll.nextbal_raw.isnull() * ll.nextbal_raw, because if it is
# NA, I'll still get the NaN.
ll['nextbal'] = tf.select([ll.nextbal_raw.notnull()], [ll.nextbal_raw], default=0)
ll2 = ll.groupby("fctrdt").agg({"fctrdt":"cnt", "nextbal":"sum", "schedbal":"sum"})
ll2['cpr'] = tf.func.smm2cpr(100 * (1 - ll.nextbal_sum / ll.schedbal_sum))
rv = ll2
rv

fctrdt  fctrdt_cnt   nextbal_sum  schedbal_sum        cpr
0  2006-08-01     1248295  2.237934e+11  2.254628e+11   8.531914
1  2006-09-01     1405223  2.525813e+11  2.543747e+11   8.139850
2  2006-10-01     1562566  2.792544e+11  2.819308e+11  10.815418
3  2006-11-01     1707353  3.059594e+11  3.089015e+11  10.849283
4  2006-12-01     1843773  3.298006e+11  3.336411e+11  12.971410
5  2007-01-01     2000769  3.577633e+11  3.618557e+11  12.758205
6  2007-02-01     2155735  3.903339e+11  3.939057e+11  10.354637
7  2007-03-01     2326005  4.242724e+11  4.286674e+11  11.632607
8  2007-04-01     2493779  4.555523e+11  4.603572e+11  11.830369
9  2007-05-01     2647677  4.851136e+11  4.901698e+11  11.699629